In [1]:
import warnings
import pandas as pd
import os
import utils

pd.set_option('display.max_rows', 300)
pd.set_option('display.max_columns', 100)
warnings.filterwarnings('ignore')

/var/folders/mp/6wd7514s0s1gfpl_csdmpfh80000gn/T/ipykernel_43572/2027364064.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [2]:
%%time

from datetime import datetime
from tqdm import tqdm
import os

test_data = {}

inp_filename = 'pi_pull_m6_2024-01-14.csv'
data_dir = 'data'

#date_cutoff = pd.to_datetime('2023-12-31')

inp_path = os.path.join(data_dir, inp_filename)
#raw_data = pd.read_csv(inp_path, nrows=N)

print(f'[INFO {datetime.now()}] Reading csv...')
raw_data = pd.read_csv(inp_path)

[INFO 2024-02-13 22:47:14.181981] Reading csv...
CPU times: user 51.6 s, sys: 1min 1s, total: 1min 53s
Wall time: 3min 41s


In [3]:
%%time

import preprocess

print(f'[INFO {datetime.now()}] Merging data...')
test_data = preprocess.merge_data_with_time(raw_data)
print(f'[INFO {datetime.now()}] Processing data...')
for ext_id in test_data.keys():
    test_data[ext_id] = preprocess.process_column_names(test_data[ext_id], ext_id)
    test_data[ext_id] = preprocess.resample_and_fill(test_data[ext_id])

print(f'[INFO {datetime.now()}] ...complete.')

[INFO 2024-02-13 22:50:56.118206] Merging data...
[INFO 2024-02-13 22:55:12.749209] Processing data...
[INFO 2024-02-13 22:55:36.189516] ...complete.
CPU times: user 3min 47s, sys: 33.3 s, total: 4min 21s
Wall time: 4min 40s


In [4]:
for key in test_data.keys():
    print(test_data[key].index.min(), test_data[key].index.max())

2023-07-17 16:06:15 2024-01-14 04:50:45
2023-07-17 16:06:15 2024-01-14 04:50:45
2023-09-20 07:20:45 2024-01-14 04:50:45
2023-07-17 16:06:15 2024-01-14 04:50:45


In [5]:
test_set = pd.concat([test_data['EX1'], test_data['EX2']])
test_set = test_set[test_set.index >= pd.to_datetime('1/1/24')]

In [6]:
import pickle

from sklearn.metrics import accuracy_score, confusion_matrix

with open('svm_grid_search_ex12_6H_basevars_only_240212.pkl', 'rb') as f:
    grid_search = pickle.load(f)

model = grid_search.best_estimator_


input_features = [
    'pressure',
    'velocity_screw_output',
    'velocity_screw',
    'temperature',
    'thrust',
    'current_screw',
    'current_conveyor',
    'velocity_conveyor'
]

X_test = test_set[input_features]

probabilities = model.predict_proba(X_test)
predictions = model.predict(X_test)

In [7]:
for prob in probabilities:
    print(prob)

[0.94104357 0.05895643]
[0.9380955 0.0619045]
[0.94203899 0.05796101]
[0.94377458 0.05622542]
[0.93796795 0.06203205]
[0.94126186 0.05873814]
[0.94278728 0.05721272]
[0.94536025 0.05463975]
[0.94571045 0.05428955]
[0.94068499 0.05931501]
[0.9478282 0.0521718]
[0.94624233 0.05375767]
[0.94146594 0.05853406]
[0.94074559 0.05925441]
[0.94273037 0.05726963]
[0.94009975 0.05990025]
[0.94781079 0.05218921]
[0.94363459 0.05636541]
[0.94613207 0.05386793]
[0.94302647 0.05697353]
[0.93890017 0.06109983]
[0.93745515 0.06254485]
[0.94191829 0.05808171]
[0.93748405 0.06251595]
[0.94146041 0.05853959]
[0.94242477 0.05757523]
[0.93965899 0.06034101]
[0.94078409 0.05921591]
[0.9389855 0.0610145]
[0.93872797 0.06127203]
[0.93859746 0.06140254]
[0.93837162 0.06162838]
[0.93967048 0.06032952]
[0.93719199 0.06280801]
[0.94026271 0.05973729]
[0.94148114 0.05851886]
[0.94149581 0.05850419]
[0.94452805 0.05547195]
[0.92521986 0.07478014]
[0.94191402 0.05808598]
[0.94030193 0.05969807]
[0.94609082 0.05390918